<a href="https://colab.research.google.com/github/TokyoYoshida/GoogleColab/blob/master/fluid_simuration.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [2]:
from google.colab import drive
drive.mount('/content/drive')
# 必要ならば以下のようにディレクトリ移動する
 

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


In [3]:
%cd /content/drive/'My Drive'/'★個人専用ファイル'/'開発用・個人サービス開発'/'GoogleColab'/

/content/drive/My Drive/★個人専用ファイル/開発用・個人サービス開発/GoogleColab


In [4]:
import pandas as pd

In [5]:
import numpy as np

In [6]:
from pprint import pprint

In [7]:
import matplotlib.pyplot as plt
%matplotlib inline

In [8]:
from matplotlib import animation, rc

In [9]:
from IPython.display import HTML

In [22]:
#移流。壁のところは速度を更新してないことに注意
def Advection(x,y,vx,vy):
    vx_after = np.zeros((x + 3, y + 2), dtype=np.float64)  # x速度
    vy_after = np.zeros((x + 2, y + 3), dtype=np.float64)  # y速度
    #x方向の移流
    for i in range(2,x+1):
        for j in range(1,y+1):
            # uが事前のx方向の速度、vが事前のy方向の速度
            u = vx[i, j]
            v = (vy[i - 1,j] + vy[i,j] + vy[i - 1,j + 1] + vy[i,j + 1]) / 4
            if (u >= 0.0) & (v >= 0.0): # xもyもプラス方向なら
                # vxは、直前のvxに対する増分を決めている。 直前のvxと、その１つ前の格子の差の半分をから、直前のvyの格子差の半分を引いている。　横方向しか進まないなら、vyはあまり関係ない。ってことは、vxは格子の最初に大きくなり、少しずつ減っていくという感じになりそう。
                vx_after[i,j] = vx[i,j] - u * (vx[i,j] - vx[i-1,j]) * DELTAT - v * (vx[i,j]-vx[i,j-1]) * DELTAT # DELTATは0.5
            if (u < 0.0) & (v >= 0.0):
                vx_after[i,j] = vx[i,j] - u * (vx[i+1,j] - vx[i,j]) * DELTAT - v * (vx[i,j]-vx[i,j-1]) * DELTAT
            if (u >= 0.0) & (v < 0.0):
                vx_after[i,j] = vx[i,j] - u * (vx[i,j] - vx[i-1,j]) * DELTAT - v * (vx[i,j+1]-vx[i,j]) * DELTAT
            if (u < 0.0) & (v < 0.0):
                vx_after[i,j] = vx[i,j] - u * (vx[i+1,j] - vx[i,j]) * DELTAT - v * (vx[i,j+1]-vx[i,j]) * DELTAT
    #y方向の移流
    for i in range(1,x+1):
        for j in range(2,y+1):
            u = (vx[i,j - 1] + vx[i + 1,j - 1] + vx[i,j] + vx[i+1,j]) / 4
            v = vy[i,j]
            if (u >= 0.0) & (v >= 0.0):
                vy_after[i,j] = vy[i,j] - u * (vy[i,j] - vy[i-1,j]) * DELTAT - v * (vy[i,j]-vy[i,j-1]) * DELTAT
            if (u < 0.0) & (v >= 0.0):
                vy_after[i,j] = vy[i,j] - u * (vy[i+1,j] - vy[i,j]) * DELTAT - v * (vy[i,j]-vy[i,j-1]) * DELTAT
            if (u >= 0.0) & (v < 0.0):
                vy_after[i,j] = vy[i,j] - u * (vy[i,j] - vy[i-1,j]) * DELTAT - v * (vy[i,j+1]-vy[i,j]) * DELTAT
            if (u < 0.0) & (v < 0.0):
                vy_after[i,j] = vy[i,j] - u * (vy[i+1,j] - vy[i,j]) * DELTAT - v * (vy[i,j+1]-vy[i,j]) * DELTAT
    vx[:,:] = vx_after.copy()
    vy[:,:] = vy_after.copy()
    return


In [92]:
def Div(x,y,vx,vy,s):
    for i in range(1,x+1):
        for j in range(1,y+1):
            s[i,j]=( -vx[i,j] -vy[i,j] +vx[i+1,j] +vy[i,j+1] )/DELTAT
    return


In [102]:
def Poisson(x,y,p,s):
    for loop in range(30):#適当に30回ループで切り上げることにする
        for i in range(1,x+1):
            for j in range(1,y+1):
                #もし壁なら、p[i,j]の圧力を代入。壁情報をbool型配列で管理しておくといろんな壁が再現できる
                if i==1:#左の壁
                    p[i-1,j]=p[i,j]
                if i==x:#右の壁
                    p[i+1,j]=p[i,j]
                if j==1:#上の壁
                    p[i,j-1]=p[i,j]
                if j==y:#下の壁
                    p[i,j+1]=p[i,j]
                p[i,j] = (1.0 - OMEGA) * p[i,j] + OMEGA / 4 * (p[i - 1,j] + p[i + 1,j] + p[i,j - 1] + p[i,j + 1] - s[i,j])
    return


In [116]:
def Rhs(x,y,vx,vy,p):
    for i in range(1,x+1):
        for j in range(1,y+1):
            vx[i,j] -= (p[i,j] - p[i - 1,j]) * DELTAT
            vy[i,j] -= (p[i,j] - p[i,j - 1]) * DELTAT
    return


In [25]:
#粒子座標の速度を抽出して座標更新
#スタガード格子なのでxとy速度場の参照がずれる
def Flowparticles(vx,vy,prt):
    for i in range(prt.shape[0]):
        xx=np.clip(prt[i,0],0.0,vx.shape[0]-2)
        yy=np.clip(prt[i,1],0.0,vy.shape[1]-2)
        ixx = np.int32(xx)
        iyy = np.int32(yy-0.5)#スタガード格子なのでいろいろずれる
        sxx = xx - ixx
        syy = (yy-0.5) - iyy
        spdx = (((1.0 - sxx) * vx[ixx,iyy] + sxx * vx[ixx+1,iyy]) * (1.0 - syy) + (
                    (1.0 - sxx) * vx[ixx,iyy+1] + sxx * vx[ixx+1,iyy+1]) * syy) * DELTAT
        ixx = np.int32(xx-0.5)#スタガード格子なのでいろいろずれる
        iyy = np.int32(yy)
        sxx = (xx-0.5) - ixx
        syy = yy - iyy
        spdy = (((1.0 - sxx) * vy[ixx,iyy] + sxx * vy[ixx+1,iyy]) * (1.0 - syy) + (
                    (1.0 - sxx) * vy[ixx,iyy+1] + sxx * vy[ixx+1,iyy+1]) * syy) * DELTAT
        prt[i, 0] += spdx
        prt[i, 1] += spdy
    return


In [127]:
fig, ax = plt.subplots()
plt.close()

In [128]:
DELTAT=0.1#Δt
OMEGA=1.8#SORの加速係数


In [129]:
x =10
y = 10

In [130]:
vx = np.zeros((x + 3, y + 2), dtype=np.float64)  # x速度
vy = np.zeros((x + 2, y + 3), dtype=np.float64)  # y速度
p = np.zeros((x + 2, y + 2), dtype=np.float64)  # 圧力
s = np.zeros((x + 2, y + 2), dtype=np.float64)  # ダイバージェンス  
prt = np.random.rand(1024, 2) * np.array((x,y),dtype=np.float64)+1  # 粒子の初期座標、x,y

In [131]:
scat = ax.scatter(prt[:,0],prt[:,1])

In [132]:
# for i in range(10):
#   scat.set_offsets(prt)
#   plt.pause(0.015)

In [133]:
# ax.set_xlim(( -4, 4))
# ax.set_ylim((-2, 2))
# line1, = ax.plot([], [], lw=2)
# line2, = ax.plot([], [], lw=2)

In [134]:
#x = np.linspace(-4, 4, 100)
#y = np.sin(x)

In [139]:
def init():
    # prt = np.random.rand(1024, 2) * np.array((x,y),dtype=np.float64)+1
    scat.set_offsets(prt)
    return (scat,)
# animation function: this is called sequentially
def animate(i):
    Advection(x, y, vx, vy)
    vx[1,1]=0.7#適当に速度固定
    vx[4,4]=0.4#適当に速度固定
    vx[5,5]=-0.4#適当に速度固定
    Div(x, y, vx, vy, s)
    Poisson(x, y, p, s)
    Rhs(x, y, vx, vy, p)
    Flowparticles(vx, vy, prt)
    scat.set_offsets(prt)
    return (scat,)


In [140]:
anim = animation.FuncAnimation(fig, animate, init_func=init, frames=100, interval=10, blit=True)

In [141]:
rc('animation', html='jshtml')

In [142]:
anim